# Economic Indicator Features

This notebook aims to explore the impact of economic features on sales. Questions this notebook aims to answer include: 
1. How does ecnomic features impact sales for items in different departments?
2. How are items individuall affected by economic indicators? 
3. What is the best way to signal the model the nature of the individual item based on this features?

An important piece of information is that 2011 is not a complete date. This is what was driving the odd rolling averages. I need to fix this everywhere. 
Like wise I have learned that the last month (2016-03) is incomplete. I will filter it now. 

My conclussion here is that after applying differencing, these features lose their predictive value as the majority of it revovled around capturing the downard trend of the sales.

# Import Packages

In [111]:
import pandas as pd
from pmdarima import auto_arima
from typing import Dict, Tuple
from tslearn.clustering import TimeSeriesKMeans
from tslearn.preprocessing import TimeSeriesScalerMeanVariance
from tslearn.metrics import dtw
import sys
import os
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import statsmodels.api as sm
import numpy as np

# Load Data From BigQuery

In [113]:
project_root = os.path.abspath(os.path.join(os.getcwd(), "..", "..", "..", ".."))
sys.path.append(project_root)

# Now you can import from core if needed
from src.core.clients.bigquery import BigQueryClient

bq_client = BigQueryClient()

sales_query = """
    SELECT 
        tgt.ctx_date_month,
        tgt.ctx_cat_id, 
        tgt.ctx_dept_id, 
        tgt.ctx_item_id,
        tgt.tgt_monthly_sales,
        tgt.tgt_monthly_sales_sum_3_next_months,
        stckt.is_stockout_tgt
    FROM `porygon-pipelines.walmart_targets_and_filters.target_store_item_monthly` tgt
    LEFT JOIN `porygon-pipelines.walmart_targets_and_filters.stockout_filter` stckt
        ON tgt.ctx_item_id = stckt.ctx_item_id
        AND tgt.ctx_store_id = stckt.ctx_store_id
        AND tgt.ctx_date_month = stckt.ctx_date_month
    LEFT JOIN `porygon-pipelines.walmart_featurestore.item_longevity_features` long
        ON tgt.ctx_item_id = long.ctx_item_id
        AND tgt.ctx_date_month = long.ctx_date_month
    WHERE 
        tgt.ctx_store_id = 'CA_1'
        AND long.fea_month_difference >= 0
        --AND stckt.is_stockout_tgt = 0
"""

# Extract data
item_sales = bq_client.load_from_query(sales_query)

#item_sales = item_sales[item_sales["tgt_monthly_sales"]>0]
item_sales = item_sales[
    (item_sales["ctx_date_month"]>=pd.to_datetime("2011-02-01"))
    & (item_sales["ctx_date_month"]<=pd.to_datetime("2015-11-01"))
     ]




INFO:src.core.clients.bigquery:BigQuery client initialized for project: porygon-pipelines
/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/google/cloud/bigquery/table.py:1994: UserWarning: BigQuery Storage module not found, fetch data with the REST endpoint instead.
  warnings.warn(
/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/google/cloud/bigquery/table.py:1994: UserWarning: BigQuery Storage module not found, fetch data with the REST endpoint instead.
  warnings.warn(
INFO:src.core.clients.bigquery:Loaded 155691 rows from custom query.
INFO:src.core.clients.bigquery:Loaded 155691 rows from custom query.


# Remove items with too many stockouts

In [114]:
stockout_percent = item_sales.groupby(
    ["ctx_item_id"]
)[["is_stockout_tgt"]].mean().reset_index()

less_than_50percent_stockouts = stockout_percent[stockout_percent["is_stockout_tgt"]<0.5][["ctx_item_id"]]

item_sales_filtered = item_sales.merge(
    less_than_50percent_stockouts,
    on = ["ctx_item_id"]
)

# Extract Item Arima and Seasonal Orders

In [115]:
# Example: Fit auto_arima to a single item's sales series
item_id_list = item_sales_filtered["ctx_item_id"].unique().tolist()
iter_num = 0

arima_order_list = []
seasonal_order_list = []
aic_list = []
for item_id in item_id_list:
    try:
        iter_num += 1
        print(iter_num)
        series = (
            item_sales_filtered[item_sales_filtered["ctx_item_id"] == item_id]
            .sort_values("ctx_date_month")["tgt_monthly_sales_sum_3_next_months"]
            .dropna()
        )

        # Fit auto_arima
        model = auto_arima(series, seasonal=True, m=12, trace=True, error_action='ignore', suppress_warnings=True)

        # Extract ARIMA order and seasonal order
        arima_order = model.order
        seasonal_order = model.seasonal_order
        aic = model.aic()

        # save results:
        arima_order_list.append(arima_order)
        seasonal_order_list.append(seasonal_order)
        aic_list.append(aic)


        print(f"ARIMA order: {arima_order}")
        print(f"Seasonal order: {seasonal_order}")
        print(f"AIC: {aic}")

    except Exception as e:
        print(f"Error processing item_id {item_id}: {e}")
        # save results:
        arima_order_list.append(np.nan)
        seasonal_order_list.append(np.nan)
        aic_list.append(np.nan)
        continue

# save results into a dataframe:
df_results = pd.DataFrame(item_id_list, columns= ["ctx_item_id"])
df_results["arima_orer"] = arima_order_list
df_results["seasonal_order"] = seasonal_order_list
df_results["aic"] = aic_list

1
Performing stepwise search to minimize aic
 ARIMA(2,0,2)(1,0,1)[12] intercept   : AIC=586.328, Time=0.12 sec
 ARIMA(0,0,0)(0,0,0)[12] intercept   : AIC=655.754, Time=0.00 sec
 ARIMA(1,0,0)(1,0,0)[12] intercept   : AIC=598.635, Time=0.05 sec
 ARIMA(0,0,1)(0,0,1)[12] intercept   : AIC=617.460, Time=0.05 sec
 ARIMA(0,0,0)(0,0,0)[12]             : AIC=755.073, Time=0.00 sec
 ARIMA(2,0,2)(0,0,1)[12] intercept   : AIC=584.132, Time=0.11 sec
 ARIMA(2,0,2)(0,0,0)[12] intercept   : AIC=582.674, Time=0.03 sec
 ARIMA(0,0,1)(0,0,1)[12] intercept   : AIC=617.460, Time=0.05 sec
 ARIMA(0,0,0)(0,0,0)[12]             : AIC=755.073, Time=0.00 sec
 ARIMA(2,0,2)(0,0,1)[12] intercept   : AIC=584.132, Time=0.11 sec
 ARIMA(2,0,2)(0,0,0)[12] intercept   : AIC=582.674, Time=0.03 sec
 ARIMA(2,0,2)(1,0,0)[12] intercept   : AIC=584.550, Time=0.10 sec
 ARIMA(1,0,2)(0,0,0)[12] intercept   : AIC=582.325, Time=0.02 sec
 ARIMA(1,0,2)(1,0,0)[12] intercept   : AIC=585.359, Time=0.08 sec
 ARIMA(1,0,2)(0,0,1)[12] interc

/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/pmdarima/arima/utils.py:117: UserWarning: Appropriate D value may not have been reached; length of seasonally-differenced array (7) is shorter than m (12). Using D=1
  warnings.warn("Appropriate D value may not have been reached; "


 ARIMA(2,0,2)(1,1,1)[12] intercept   : AIC=inf, Time=0.13 sec
 ARIMA(0,0,0)(0,1,0)[12] intercept   : AIC=93.728, Time=0.00 sec
 ARIMA(1,0,0)(1,1,0)[12] intercept   : AIC=inf, Time=0.06 sec
 ARIMA(0,0,1)(0,1,1)[12] intercept   : AIC=inf, Time=0.02 sec
 ARIMA(0,0,0)(0,1,0)[12]             : AIC=104.994, Time=0.00 sec
 ARIMA(0,0,0)(1,1,0)[12] intercept   : AIC=95.728, Time=0.01 sec
 ARIMA(0,0,0)(0,1,1)[12] intercept   : AIC=inf, Time=0.03 sec
 ARIMA(0,0,0)(1,1,1)[12] intercept   : AIC=inf, Time=0.07 sec
 ARIMA(1,0,0)(0,1,0)[12] intercept   : AIC=92.347, Time=0.02 sec
 ARIMA(1,0,0)(0,1,1)[12] intercept   : AIC=inf, Time=0.04 sec
 ARIMA(1,0,0)(1,1,1)[12] intercept   : AIC=95.595, Time=0.08 sec
 ARIMA(2,0,0)(0,1,0)[12] intercept   : AIC=94.009, Time=0.03 sec
 ARIMA(1,0,1)(0,1,0)[12] intercept   : AIC=inf, Time=0.02 sec
 ARIMA(0,0,1)(0,1,0)[12] intercept   : AIC=inf, Time=0.01 sec
 ARIMA(2,0,1)(0,1,0)[12] intercept   : AIC=10.000, Time=0.01 sec
 ARIMA(1,0,0)(0,1,0)[12] intercept   : AIC=92.34

/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/statsmodels/tsa/statespace/sarimax.py:1901: RuntimeWarning: divide by zero encountered in reciprocal
  return np.roots(self.polynomial_reduced_ar)**-1
/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/statsmodels/tsa/statespace/sarimax.py:1908: RuntimeWarning: divide by zero encountered in reciprocal
  return np.roots(self.polynomial_reduced_ma)**-1
/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/statsmodels/tsa/statespace/sarimax.py:1901: RuntimeWarning: divide by zero encountered in reciprocal
  return np.roots(self.polynomial_reduced_ar)**-1
/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/statsmodels/tsa/statespace/sarimax.py:1908: RuntimeWarning: divide by zero encountered in reciprocal
  return np.roots(self.polynomial_reduced_ma)**-1
/Users/anapreciado/Desktop/porygon-demand-fo

 ARIMA(2,0,1)(1,1,0)[12] intercept   : AIC=12.000, Time=0.03 sec
 ARIMA(2,0,1)(0,1,1)[12] intercept   : AIC=12.000, Time=0.03 sec
 ARIMA(2,0,1)(1,1,1)[12] intercept   : AIC=14.000, Time=0.03 sec
 ARIMA(3,0,1)(0,1,0)[12] intercept   : AIC=12.000, Time=0.02 sec
 ARIMA(2,0,2)(0,1,0)[12] intercept   : AIC=96.800, Time=0.05 sec
 ARIMA(1,0,2)(0,1,0)[12] intercept   : AIC=96.080, Time=0.04 sec
 ARIMA(3,0,0)(0,1,0)[12] intercept   : AIC=10.000, Time=0.02 sec


...

 ARIMA(2,0,1)(0,1,0)[12] intercept   : AIC=inf, Time=0.10 sec
 ARIMA(3,0,2)(0,1,0)[12] intercept   : AIC=14.000, Time=0.04 sec
 ARIMA(2,0,3)(0,1,0)[12] intercept   : AIC=inf, Time=0.06 sec
 ARIMA(1,0,1)(0,1,0)[12] intercept   : AIC=80.667, Time=0.01 sec
 ARIMA(1,0,3)(0,1,0)[12] intercept   : AIC=inf, Time=0.06 sec


/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/statsmodels/tsa/statespace/sarimax.py:1901: RuntimeWarning: divide by zero encountered in reciprocal
  return np.roots(self.polynomial_reduced_ar)**-1
/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/statsmodels/tsa/statespace/sarimax.py:1908: RuntimeWarning: divide by zero encountered in reciprocal
  return np.roots(self.polynomial_reduced_ma)**-1


 ARIMA(3,0,1)(0,1,0)[12] intercept   : AIC=inf, Time=0.18 sec
 ARIMA(3,0,3)(0,1,0)[12] intercept   : AIC=inf, Time=0.29 sec
 ARIMA(2,0,2)(0,1,0)[12]             : AIC=inf, Time=0.07 sec

Best model:  ARIMA(2,0,2)(0,1,0)[12] intercept
Total fit time: 1.133 seconds
ARIMA order: (2, 0, 2)
Seasonal order: (0, 1, 0, 12)
AIC: 12.0
2073
Performing stepwise search to minimize aic
 ARIMA(2,0,2)(1,0,1)[12] intercept   : AIC=inf, Time=0.18 sec
 ARIMA(0,0,0)(0,0,0)[12] intercept   : AIC=176.049, Time=0.01 sec
 ARIMA(1,0,0)(1,0,0)[12] intercept   : AIC=163.483, Time=0.08 sec
 ARIMA(0,0,1)(0,0,1)[12] intercept   : AIC=170.657, Time=0.03 sec
 ARIMA(0,0,0)(0,0,0)[12]             : AIC=221.549, Time=0.00 sec
 ARIMA(1,0,0)(0,0,0)[12] intercept   : AIC=161.486, Time=0.01 sec
 ARIMA(1,0,0)(0,0,1)[12] intercept   : AIC=163.483, Time=0.04 sec
 ARIMA(1,0,0)(1,0,1)[12] intercept   : AIC=inf, Time=0.14 sec
 ARIMA(2,0,0)(0,0,0)[12] intercept   : AIC=160.452, Time=0.03 sec
 ARIMA(2,0,0)(1,0,0)[12] intercept   : 

/Users/anapreciado/Desktop/porygon-demand-forecasting/venv/lib/python3.13/site-packages/pmdarima/arima/utils.py:117: UserWarning: Appropriate D value may not have been reached; length of seasonally-differenced array (7) is shorter than m (12). Using D=1
  warnings.warn("Appropriate D value may not have been reached; "


 ARIMA(2,0,2)(1,1,1)[12] intercept   : AIC=inf, Time=0.32 sec
 ARIMA(0,0,0)(0,1,0)[12] intercept   : AIC=56.859, Time=0.01 sec
 ARIMA(1,0,0)(1,1,0)[12] intercept   : AIC=inf, Time=0.21 sec
 ARIMA(0,0,1)(0,1,1)[12] intercept   : AIC=58.949, Time=0.11 sec
 ARIMA(0,0,0)(0,1,0)[12]             : AIC=55.403, Time=0.02 sec
 ARIMA(0,0,0)(1,1,0)[12] intercept   : AIC=58.859, Time=0.02 sec
 ARIMA(0,0,0)(0,1,1)[12] intercept   : AIC=58.858, Time=0.06 sec
 ARIMA(0,0,0)(1,1,1)[12] intercept   : AIC=60.858, Time=0.11 sec
 ARIMA(1,0,0)(0,1,0)[12] intercept   : AIC=56.148, Time=0.02 sec
 ARIMA(0,0,1)(0,1,0)[12] intercept   : AIC=56.950, Time=0.02 sec
 ARIMA(1,0,1)(0,1,0)[12] intercept   : AIC=57.704, Time=0.01 sec

Best model:  ARIMA(0,0,0)(0,1,0)[12]          
Total fit time: 0.928 seconds
ARIMA order: (0, 0, 0)
Seasonal order: (0, 1, 0, 12)
AIC: 55.402537142096435
2076
Performing stepwise search to minimize aic
 ARIMA(2,0,2)(1,0,1)[12] intercept   : AIC=inf, Time=0.18 sec
 ARIMA(0,0,0)(0,0,0)[12] i

In [117]:
df_results["arima_order_p"] = df_results["arima_orer"].apply(lambda x: x[0] if pd.notnull(x) else np.nan)
df_results["arima_order_d"] = df_results["arima_orer"].apply(lambda x: x[1] if pd.notnull(x) else np.nan)
df_results["arima_order_q"] = df_results["arima_orer"].apply(lambda x: x[2] if pd.notnull(x) else np.nan)

df_results["seasonal_order_p"] = df_results["seasonal_order"].apply(lambda x: x[0] if pd.notnull(x) else np.nan)
df_results["seasonal_order_d"] = df_results["seasonal_order"].apply(lambda x: x[1] if pd.notnull(x) else np.nan)
df_results["seasonal_order_q"] = df_results["seasonal_order"].apply(lambda x: x[2] if pd.notnull(x) else np.nan)
df_results["seasonal_order_m"] = df_results["seasonal_order"].apply(lambda x: x[3] if pd.notnull(x) else np.nan)
df_results.to_csv(
    "autoarima_results_per_item.csv"
)

In [122]:
df_results_analysis = df_results.copy()
df_results_analysis["ctx_dept_id"] = df_results_analysis["ctx_item_id"].apply(lambda x: f"{x.split('_')[0]}_{x.split('_')[1]}")
df_tgt_with_orders = item_sales_filtered.merge(
    df_results_analysis,
    on = ["ctx_item_id"]
)

# Arima Order Patterns - Differencing: 

- Most of them did not require differencing. Almost one third requires differencing.
- Would be good to tell the model when is a trend present and maybe differencing values. 

The questions tarts to be what is the best way to tell te model that the item has a trend. 
- Correlation features created ealier seem to be too noisy for this. 
- Consider adding slope features like the ones below.

# Conclussion

I will compute the arima order for each item as a feature then provide the model with the required values. 

1. Differencing: This will be a feature with the differencing order. I will include then slope features for the model as well.

2. AR: This will be a feature with the order. I am already providing the lagged values. I will also provide with the differenced lagged values for the model to use. 

3. Seasonality: I will provide the seasonal order. I will provide with the value last year. 